### Flow Matching Ergodic Coverage Tutorial
#### 3D coverage using Sinkhorn divergence flow with the 3D aircraft dynamics

This tutorial uses [`lqrax`](https://github.com/MaxMSun/lqrax/tree/main) to solve the continuous time Riccati equation for the LQ flow matching problem and [`ott`](https://github.com/ott-jax/ott) to compute the Sinkhorn divergence.

In [1]:
import time
from tqdm.notebook import tqdm
import matplotlib.pyplot as plt
import jax.numpy as jnp
import os
import numpy as np

from jax import jit, grad, vmap, jacfwd
from jax.scipy.stats import gaussian_kde as kde
from jax.scipy.stats import multivariate_normal as mvn
import jax
cpu = jax.devices("cpu")[0]
try:
    gpu = jax.devices("cuda")[0]
except:
    gpu = cpu
jnp.set_printoptions(precision=4)

try:
    from lqrax import LQR
except:
    %pip install lqrax
    from lqrax import LQR

try:
    import ott 
except:
    %pip install ott-jax 
    import ott 
from ott.geometry import pointcloud
from ott.geometry.costs import PNormP
from ott.tools.sinkhorn_divergence import sinkhorn_divergence

In [2]:
def visualize_3d(x0, x_traj, tgt_samples):
    import numpy as np
    import plotly.graph_objects as go

    traj_color = "#ff7f0e"
    sample_color = "#9467bd"
    quad_color = "black"
    arm_length=0.08

    fig = go.Figure()
    # samples
    fig.add_trace(go.Scatter3d(
        x=tgt_samples[:, 0], y=tgt_samples[:, 1], z=tgt_samples[:, 2],
        mode='markers',
        marker=dict(color=sample_color, size=3, opacity=0.1)
    ))
    # trajectory
    fig.add_trace(go.Scatter3d(
        x=x_traj[:, 0], y=x_traj[:, 1], z=x_traj[:, 2],
        mode='lines+markers',
        line=dict(color=traj_color),
        marker=dict(color=traj_color, size=3)
    ))
    # quadcopter arms (two crossing lines)
    fig.add_trace(go.Scatter3d(
        x=[x0[0]-arm_length, x0[0]+arm_length],
        y=[x0[1],        x0[1]],
        z=[x0[2],        x0[2]],
        mode='lines',
        line=dict(color=quad_color, width=8)
    ))
    fig.add_trace(go.Scatter3d(
        x=[x0[0],        x0[0]],
        y=[x0[1]-arm_length, x0[1]+arm_length],
        z=[x0[2],        x0[2]],
        mode='lines',
        line=dict(color=quad_color, width=8)
    ))
    
    fig.add_trace(go.Scatter3d(
        x=[x0[0]],
        y=[x0[1]-arm_length],
        z=[x0[2]],
        mode='markers',
        marker=dict(color='black', size=5)
    ))
    fig.add_trace(go.Scatter3d(
        x=[x0[0]],
        y=[x0[1]+arm_length],
        z=[x0[2]],
        mode='markers',
        marker=dict(color='black', size=5)
    ))
    fig.add_trace(go.Scatter3d(
        x=[x0[0]-arm_length],
        y=[x0[1]],
        z=[x0[2]],
        mode='markers',
        marker=dict(color='black', size=5)
    ))
    fig.add_trace(go.Scatter3d(
        x=[x0[0]+arm_length],
        y=[x0[1]],
        z=[x0[2]],
        mode='markers',
        marker=dict(color='black', size=5)
    ))

    # propeller rings
    prop_radius = arm_length * 0.5     # radius of each little ring
    theta = np.linspace(0, 2*np.pi, 30)
    # offsets of the four motors from center
    offsets = [(arm_length,  0),
               (-arm_length,  0),
               (0,  arm_length),
               (0, -arm_length)]
    for dx, dy in offsets:
        cx, cy, cz = x0[0] + dx, x0[1] + dy, x0[2]
        fig.add_trace(go.Scatter3d(
            x=cx + prop_radius * np.cos(theta),
            y=cy + prop_radius * np.sin(theta),
            z=cz + np.zeros_like(theta),
            mode='lines',
            line=dict(color=quad_color, width=4)
        ))
    
    fig.add_trace(go.Scatter3d(x=[x0[0]], y=[x0[1]], z=[
        x0[2]], mode='markers', marker=dict(color='black', size=10)))

    fig.update_layout(
        scene=dict(
            camera=dict(eye=dict(x=0.7, y=0.7, z=0.7)),
            xaxis=dict(range=[-0.6, 0.6], showgrid=False, visible=False),
            yaxis=dict(range=[-0.6, 0.6], showgrid=False, visible=False),
            zaxis=dict(range=[-0.6, 0.6], showgrid=False, visible=False),
            aspectmode='cube'
        ),
        paper_bgcolor='white',
        scene_bgcolor='white',
        margin=dict(l=0, r=0, t=0, b=0),
        showlegend=False
    )
    fig.show()

In [3]:
import urllib.request

object_list = ["bunny", "airplane", "armadillo", "chair"]
obj_idx = 0

object = object_list[obj_idx]
print(f'object: {object}')

resp = urllib.request.urlopen(
    f"https://raw.githubusercontent.com/MurpheyLab/lqr-flow-matching/refs/heads/main/tutorials/test_objects/3d/{object}.txt")
tgt_samples_dense = np.loadtxt(resp)[:, :3]


tgt_samples = tgt_samples_dense[:3000]
tgt_samples = jnp.array(tgt_samples)
num_samples = tgt_samples.shape[0]
print(f'samples.shape: {tgt_samples.shape}')

object: bunny
samples.shape: (3000, 3)


In [4]:
class AircraftLQR(LQR):
    def __init__(self, dt, x_dim, u_dim, Q, R):
        super().__init__(dt, x_dim, u_dim, Q, R)

    def dyn(self, xt, ut):
        x, y, z, psi, phi, v = xt
        xdot = jnp.array([
            v * jnp.cos(phi) * jnp.cos(psi),
            v * jnp.cos(phi) * jnp.sin(psi),
            v * jnp.sin(phi),
            ut[0],
            ut[1],
            ut[2]
        ])
        return xdot

In [5]:
Q = jnp.diag(jnp.array([
    1.0, 1.0, 1.0, 1e-03, 1e-03, 1e-03,
]))
R = jnp.diag(jnp.array([0.01, 0.01, 0.1]))

aircraft_lqr = AircraftLQR(dt=0.05, x_dim=6, u_dim=3, Q=Q, R=R)

# lqr solving on CPU is faster
linearize_dyn = jit(aircraft_lqr.linearize_dyn, device=cpu)
solve_lqr = jit(aircraft_lqr.solve, device=cpu)

In [6]:
tsteps = 600

x0 = jnp.array([
    -0.2, -0.2, 0.0, jnp.pi/4.0, 0.0, 0.02
])
u_traj = jnp.zeros((tsteps, 3))
x_traj, A_traj, B_traj = linearize_dyn(x0, u_traj)

In [7]:
visualize_3d(x0, x_traj, tgt_samples_dense)

In [8]:
def sinkhorn_div(x_samples):
    """Return the OT cost and OT output given a geometry"""
    eps = 0.005
    cost_fn = PNormP(p=1)
    sinkhorn_cost = sinkhorn_divergence(
        pointcloud.PointCloud,
        x_samples[:,:3],
        tgt_samples[:,:3],
        cost_fn=cost_fn,
        epsilon=eps
    )[0]
    return sinkhorn_cost * 1e3


sinkhorn_grad = jit(lambda _xs: -1.0 *
                    grad(sinkhorn_div)(_xs), device=gpu)

In [9]:
sinkhorn_dx_traj = sinkhorn_grad(x_traj)
sinkhorn_dx_traj = np.array(sinkhorn_dx_traj)
# note that the dimension of the descent direction matches the trajectory
print(
    f'sinkhorn_dx_traj .shape: {sinkhorn_dx_traj.shape} == x_traj.shape: {x_traj.shape}')

sinkhorn_dx_traj .shape: (600, 6) == x_traj.shape: (600, 6)


In [10]:
# Solve the flow matching ergodic coverage problem
# (use a smaller step size here for smoother animation)
z0 = jnp.zeros(6)
step_size = 0.01
num_iters = 600
x_traj_list = []
for i in tqdm(range(num_iters)):
    x_traj, A_traj, B_traj = linearize_dyn(x0, u_traj)
    sinkhorn_dx_traj = sinkhorn_grad(x_traj)
    v_traj, z_traj = solve_lqr(z0, A_traj, B_traj, sinkhorn_dx_traj)
    u_traj += step_size * v_traj
    x_traj_list.append(np.array(x_traj))
final_x_traj = aircraft_lqr.traj_sim(x0, u_traj)
x_traj_list.append(final_x_traj)
x_traj_list = np.array(x_traj_list)

  0%|          | 0/600 [00:00<?, ?it/s]

In [11]:
visualize_3d(x0, final_x_traj, tgt_samples_dense)

In [12]:
def visualize_3d_animation(x0, x_traj_list, tgt_samples):
    import plotly.graph_objects as go
    traj_color = "#ff7f0e"
    sample_color = "#9467bd"
    quad_color = "black"
    arm_length = 0.08
    
    fig = go.Figure()

    fig.update_layout(
        margin=dict(l=10, r=10, t=30, b=60),
        plot_bgcolor="white",
        width=800,    # square canvas
        height=600
    )

    fig.add_trace(go.Scatter3d(
        x=tgt_samples[:, 0], y=tgt_samples[:, 1], z=tgt_samples[:, 2],
        mode='markers',
        marker=dict(size=3, color=sample_color, opacity=0.1),
        showlegend=False
    ))
    fig.add_trace(go.Scatter3d(
        x=x_traj_list[-1][:, 0], y=x_traj_list[-1][:, 1], z=x_traj_list[-1][:, 2],
        mode='lines+markers',
        line=dict(color=traj_color),
        marker=dict(size=3, color=traj_color),
        showlegend=False
    ))
    
    # quadcopter arms (two crossing lines)
    fig.add_trace(go.Scatter3d(
        x=[x0[0]-arm_length, x0[0]+arm_length],
        y=[x0[1],        x0[1]],
        z=[x0[2],        x0[2]],
        mode='lines',
        line=dict(color=quad_color, width=8)
    ))
    fig.add_trace(go.Scatter3d(
        x=[x0[0],        x0[0]],
        y=[x0[1]-arm_length, x0[1]+arm_length],
        z=[x0[2],        x0[2]],
        mode='lines',
        line=dict(color=quad_color, width=8)
    ))

    fig.add_trace(go.Scatter3d(
        x=[x0[0]],
        y=[x0[1]-arm_length],
        z=[x0[2]],
        mode='markers',
        marker=dict(color='black', size=5)
    ))
    fig.add_trace(go.Scatter3d(
        x=[x0[0]],
        y=[x0[1]+arm_length],
        z=[x0[2]],
        mode='markers',
        marker=dict(color='black', size=5)
    ))
    fig.add_trace(go.Scatter3d(
        x=[x0[0]-arm_length],
        y=[x0[1]],
        z=[x0[2]],
        mode='markers',
        marker=dict(color='black', size=5)
    ))
    fig.add_trace(go.Scatter3d(
        x=[x0[0]+arm_length],
        y=[x0[1]],
        z=[x0[2]],
        mode='markers',
        marker=dict(color='black', size=5)
    ))

    # propeller rings
    prop_radius = arm_length * 0.5     # radius of each little ring
    theta = np.linspace(0, 2*np.pi, 30)
    # offsets of the four motors from center
    offsets = [(arm_length,  0),
               (-arm_length,  0),
               (0,  arm_length),
               (0, -arm_length)]
    for dx, dy in offsets:
        cx, cy, cz = x0[0] + dx, x0[1] + dy, x0[2]
        fig.add_trace(go.Scatter3d(
            x=cx + prop_radius * np.cos(theta),
            y=cy + prop_radius * np.sin(theta),
            z=cz + np.zeros_like(theta),
            mode='lines',
            line=dict(color=quad_color, width=4)
        ))

    fig.add_trace(go.Scatter3d(x=[x0[0]], y=[x0[1]], z=[
        x0[2]], mode='markers', marker=dict(color='black', size=10)))

    frames = []
    skip = 1
    for i, traj in enumerate(x_traj_list[::skip]):
        frames.append(go.Frame(
            name=str(i*skip),
            data=[go.Scatter3d(
                x=traj[:, 0], y=traj[:, 1], z=traj[:, 2],
                mode='lines+markers',
                line=dict(color=traj_color),
                marker=dict(size=3, color=traj_color),
                showlegend=False
            )],
            traces=[1]
        ))
    fig.frames = frames

    steps = [
        dict(
            method='animate',
            args=[[str(i)], dict(mode='immediate', frame=dict(
                duration=0, redraw=True), transition=dict(duration=0))],
            label=str(i)
        ) for i in range(len(x_traj_list))
    ]
    
    # 5) Slider (narrow, centered)
    steps = [
        dict(method="animate",
            args=[[str(i)], dict(mode="immediate",
                                frame=dict(duration=0, redraw=True),
                                transition=dict(duration=0))],
            label=str(i))
        for i in range(len(x_traj_list))
    ]
    fig.update_layout(
        sliders=[dict(
            active=len(x_traj_list)-1,
            y=-0.05,
            x=0.5,
            xanchor="center",
            pad=dict(t=10),
            len=0.5,
            steps=steps,
            currentvalue=dict(prefix="Iteration: ", font=dict(size=12))
        )]
    )

    # 6) Start / Pause / Reset buttons (row, centered, moved down)
    fig.update_layout(
        updatemenus=[dict(
            type="buttons",
            direction="left",
            x=0.5,
            y=-0.25,
            xanchor="center",
            yanchor="top",
            pad=dict(r=10, t=10),
            buttons=[
                dict(label="Start",
                    method="animate",
                    args=[None, dict(frame=dict(duration=10, redraw=True),
                                    transition=dict(duration=0),
                                    fromcurrent=True,
                                    mode="immediate")]),
                dict(label="Pause",
                    method="animate",
                    args=[[None], dict(frame=dict(duration=0, redraw=False),
                                        transition=dict(duration=0),
                                        mode="immediate")]),
                dict(label="Reset",
                    method="animate",
                    args=[[str(0)], dict(frame=dict(duration=0, redraw=True),
                                        transition=dict(duration=0),
                                        mode="immediate")])
            ]
        )]
    )

    fig.update_layout(
        scene=dict(
            camera=dict(eye=dict(x=0.7, y=0.7, z=0.7)),
            xaxis=dict(range=[-0.6, 0.6], showgrid=False, visible=False),
            yaxis=dict(range=[-0.6, 0.6], showgrid=False, visible=False),
            zaxis=dict(range=[-0.6, 0.6], showgrid=False, visible=False),
            aspectmode='cube'
        ),
        paper_bgcolor='white',
        scene_bgcolor='white',
        showlegend=False
    )
    
    fig.show()
    # fig.write_html(
    #     f"sinkhorn3d_{object}.html",
    #     include_plotlyjs="cdn",
    #     full_html=True,
    #     auto_play=False
    # )

In [13]:
visualize_3d_animation(x0, x_traj_list[::2], tgt_samples_dense)